In [ ]:
# Hier werden alle verwendeten Pythonmodule importiert
import Datenbank
import Import
import importlib
import Koordinatentransformationen
import sqlite3
import Funktionales_Modell
import Berechnungen

In [ ]:
importlib.reload(Datenbank)
importlib.reload(Import)
# Anlegen der Datenbank, wenn nicht vorhanden
pfad_datenbank = r"Campusnetz.db"
Datenbank.Datenbank_anlegen(pfad_datenbank)

# Import vervollständigen
imp = Import.Import(pfad_datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)

In [ ]:
# Import der Koordinatendatei(en) vom Tachymeter
pfad_datei = r"Daten\campsnetz_koordinaten_bereinigt.csv"
imp.import_koordinaten_lh_tachymeter(pfad_datei)

In [ ]:
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)
# Transformationen in ETRS89 / DREF91 Realisierung 2025
print(db_zugriff.get_koordinaten("naeherung_lh"))

In [ ]:
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)
# Transformationen in ETRS89 / DREF91 Realisierung 2025
print(db_zugriff.get_koordinaten("naeherung_us"))

In [ ]:
# ToDo: Sobald GNSS vorliegend Koordinaten im ETRS89 / DREF 91 (2025) daraus berechnen!
liste_koordinaten_naeherung_us_alt = {
    10001: (3794874.98408291, 546741.751930012, 5079995.3838),
    10002: (3794842.53340714, 546726.907150697, 5080039.8778),
    10008: (3794757.41294192, 546742.822339098, 5080107.3198),
    10012: (3794827.11937161, 546801.412652168, 5080028.5852),
    10026: (3794727.06042449, 546823.571170112, 5080134.2029),
    10028: (3794862.91900719, 546904.943464041, 5079920.8994),
    10037: (3794774.14751515, 546955.423068316, 5079960.9426),
    10044: (3794725.78597473, 546954.557211544, 5080009.9234),
    10054: (3794852.07416848, 547094.399826613, 5079715.1737),
    10059: (3794710.34348443, 547075.630380075, 5080119.6491),
}

liste_koordinaten_naeherung_us_V2 = {
    10001: (3794874.984, 546741.752, 5080029.990),
    10002: (3794842.533, 546726.907, 5080071.133),
    10008: (3794757.413, 546742.822, 5080135.400),
    10012: (3794827.119, 546801.413, 5080065.404),
    10026: (3794727.060, 546823.571, 5080179.951),
    10028: (3794862.919, 546904.943, 5079963.214),
    10037: (3794774.148, 546955.423, 5080040.520),
    10044: (3794725.786, 546954.557, 5080084.411),
    10054: (3794852.074, 547094.400, 5079771.845),
    10059: (3794710.343, 547075.630, 5080153.653),
}

liste_koordinaten_naeherung_us = {
    10001: (3794874.984, 546741.752, 5080029.990),
    10002: (3794842.533, 546726.907, 5080071.133),
    10037: (3794774.148, 546955.423, 5080040.520),
    10044: (3794725.786, 546954.557, 5080084.411),
}


con = sqlite3.connect(pfad_datenbank)
cursor = con.cursor()
sql = """
UPDATE Netzpunkte
SET naeherungx_us = ?, naeherungy_us = ?, naeherungz_us = ?
WHERE punktnummer = ?
"""
for punktnummer, (x, y, z) in liste_koordinaten_naeherung_us.items():
    cursor.execute(sql, (x, y, z, punktnummer))
con.commit()
cursor.close()
con.close()

In [ ]:
# ToDo: Sobald GNSS-Daten vorliegen und die Berechnungen richtig sind, aufräumen!!!

importlib.reload(Koordinatentransformationen)
trafos = Koordinatentransformationen.Transformationen(pfad_datenbank)


import numpy as np

import itertools
import numpy as np
import sympy as sp

db = Datenbank.Datenbankzugriff(pfad_datenbank)
dict_ausgangssystem = db.get_koordinaten("naeherung_lh", "Dict")
dict_zielsystem = db.get_koordinaten("naeherung_us", "Dict")

gemeinsame_punktnummern = sorted(set(dict_ausgangssystem.keys()) & set(dict_zielsystem.keys()))
anzahl_gemeinsame_punkte = len(gemeinsame_punktnummern)

liste_punkte_ausgangssystem = [dict_ausgangssystem[i] for i in gemeinsame_punktnummern]
liste_punkte_zielsystem = [dict_zielsystem[i] for i in gemeinsame_punktnummern]

def dist(a, b):
    return float((a - b).norm())

print("d(p2,p1)=", dist(liste_punkte_ausgangssystem[1], liste_punkte_ausgangssystem[0]))
print("d(P2,P1)=", dist(liste_punkte_zielsystem[1], liste_punkte_zielsystem[0]))
print("m0 ~", dist(liste_punkte_zielsystem[1], liste_punkte_zielsystem[0]) /
               dist(liste_punkte_ausgangssystem[1], liste_punkte_ausgangssystem[0]))


def dist(a, b):
    return float((a - b).norm())

ratios = []
pairs = list(itertools.combinations(range(len(liste_punkte_ausgangssystem)), 2))

for i, j in pairs:
    d_loc = dist(liste_punkte_ausgangssystem[i], liste_punkte_ausgangssystem[j])
    d_ecef = dist(liste_punkte_zielsystem[i], liste_punkte_zielsystem[j])
    if d_loc > 1e-6:
        ratios.append(d_ecef / d_loc)

print("Anzahl Ratios:", len(ratios))
print("min/mean/max:", min(ratios), sum(ratios)/len(ratios), max(ratios))
print("std:", float(np.std(ratios)))

S_loc = sum(liste_punkte_ausgangssystem, sp.Matrix([0,0,0])) / anzahl_gemeinsame_punkte
S_ecef = sum(liste_punkte_zielsystem, sp.Matrix([0,0,0])) / anzahl_gemeinsame_punkte

print("S_loc:", S_loc)
print("S_ecef:", S_ecef)
print("Delta:", (S_ecef - S_loc).evalf(6))


def dist(a, b):
    return float((a - b).norm())

n = len(liste_punkte_ausgangssystem)

scores = []
for i in range(n):
    d_loc = []
    d_ecef = []
    for j in range(n):
        if i == j:
            continue
        d_loc.append(dist(liste_punkte_ausgangssystem[i], liste_punkte_ausgangssystem[j]))
        d_ecef.append(dist(liste_punkte_zielsystem[i], liste_punkte_zielsystem[j]))

    d_loc = np.array(d_loc)
    d_ecef = np.array(d_ecef)

    # Verhältnisvektor; robust gegen Nullschutz
    r = d_ecef / np.where(d_loc == 0, np.nan, d_loc)

    # Streuung der Ratios für Punkt i
    score = np.nanstd(r)
    scores.append(score)

for pn, sc in sorted(zip(gemeinsame_punktnummern, scores), key=lambda x: -x[1]):
    print(pn, round(sc, 4))



transformationsparameter = trafos.Helmerttransformation_Euler_Transformationsparameter_berechne()

In [ ]:
importlib.reload(Koordinatentransformationen)
trafos = Koordinatentransformationen.Transformationen(pfad_datenbank)

koordinaten_transformiert = trafos.Helmerttransformation(transformationsparameter)
print(koordinaten_transformiert)

In [ ]:
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)

db_zugriff.set_koordinaten(koordinaten_transformiert, "naeherung_us")

In [ ]:
# Importieren der tachymetrischen Beobachtungen
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)

db_zugriff.get_instrument("Tachymeter")
db_zugriff.set_instrument("Tachymeter", "Trimble S9")
db_zugriff.get_instrument("Tachymeter")

In [ ]:
# Importieren der tachymetrischen Beobachtungen
importlib.reload(Import)
imp = Import.Import(pfad_datenbank)

pfad_datei_tachymeterbeobachtungen = r"Daten\campsnetz_beobachtungen_bereinigt.csv"

imp.import_beobachtungen_tachymeter(pfad_datei_tachymeterbeobachtungen, 1)

In [ ]:
# Jacobimatrix aufstellen
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)

# Parameter des GRS80-ellipsoids (Bezugsellipsoid des ETRS89 / DREF 91 (2025)
# ToDo: Quelle mit möglichst genauen Parametern heraussuchen!
a = 6378137.0 #m
b = 63567552.314 #m

importlib.reload(Funktionales_Modell)
fm = Funktionales_Modell.FunktionalesModell(pfad_datenbank, a, b)

#db_zugriff.get_beobachtungen_id_standpunkt_zielpunkt("tachymeter_distanz")
Jacobimatrix_symbolisch = fm.jacobi_matrix_symbolisch()[0]
Jacobimatrix_symbolisch_liste_unbekannte = fm.jacobi_matrix_symbolisch()[1]
Jacobimatrix_symbolisch_liste_zeilenbeschriftungen = fm.jacobi_matrix_symbolisch()[2]

In [ ]:
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)
importlib.reload(Funktionales_Modell)
fm = Funktionales_Modell.FunktionalesModell(pfad_datenbank, a, b)




fm.jacobi_matrix_zahlen_iteration_0(Jacobimatrix_symbolisch, "naeherung_us", Jacobimatrix_symbolisch_liste_unbekannte, Jacobimatrix_symbolisch_liste_zeilenbeschriftungen)